### Steps:
- 1. tokenize it and choose whether to do further pre-processing or filtering.
- 2. The second step is to produce the features in the notation of the NLTK.
    - a. write feature functions
    - b. start with the “bag-of-words” features where you collect all the words in the corpus and select some number of most frequent words to be the word features.
- 3. use the NLTK Naïve Bayes classifier to train and test a classifier on your feature sets. You should use cross-validation to obtain precision, recall and F-measure scores.
    - a. you can choose to produce the features as a csv file and use sklearn to train and test a classifier, using cross-validation scores.
- 4. For a base level completion of experiments, carry out at least several experiments where you
use two different sets of features and compare the results.
EXAMPLE: Take the
unigram word features as a baseline and see if the features you designed improve the accuracy of
the classification.

Some of the types of experiments:
- filter by stopwords or other pre-processing methods
- representing negation (if using twitter data, note the difference in tokenization)
- using a sentiment lexicon with scores or counts: Subjectivity
- different sizes of vocabularies

- POS tag features
- 5. define at least one “new” feature function not given in class. Also you should try to
combine some of the earlier features, e.g. to use unigrams, bigrams, POS tag counts, and
sentiment word counts all in one feature set. Examples of new features:
    - Use the LIWC sentiment lexicon
    - combine the use of sentiment lexicons
    - use a different representation of negation, for example, carrying the scope of the negation
work over to the next punctuation
- 6. Do something from this list:
using Sklearn classifiers with features produced in NLTK.
- • using an additional type of lexicon besides Subjectivity or LIWC
- • in addition to using cross-validation on the training set, train the classifier on the entire
training set and test it on a separately available test set (only the SemEval data has these)
o note that you must save the vocabulary from the training set and use the same for
creating feature sets for the test data

- • implement additional features
    - in the email dataset, use word frequency or tfidf scores as the values of the word
features, instead of Boolean values
    - use POS tagging from the ARK on Twitter
    - twitter emoticons or other features based on internet usage or informal text, such
as repeated letters, or all caps words

In [87]:
import warnings
warnings.filterwarnings('ignore')

In [88]:
# print all outputs, not just the last one
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [89]:
import pandas as pd
import sklearn as sk
from nltk import *
import re
import numpy as np
import random
import matplotlib.pyplot as plt
from nltk import sent_tokenize
from prettytable import PrettyTable

In [90]:
test = pd.read_table('./sentiment-analysis-on-movie-reviews/test.tsv')
train = pd.read_table('./sentiment-analysis-on-movie-reviews/train.tsv')

In [91]:
# drop sendenceId dupes
train.drop_duplicates(subset="SentenceId", keep="first", inplace=True)

### Add more columns to analyze the data

Clone train dataframe and add additional columns

In [92]:
train_additional_cols = pd.DataFrame(train)

train_additional_cols["word_tokens"] = np.nan
train_additional_cols["phrase_length"] = np.nan
train_additional_cols["POS_tags"] = np.nan


Remove all rows where Phrase is 1 char long

In [93]:
train_additional_cols[:76]

PhraseId  SentenceId                                             Phrase  \
0            1           1  A series of escapades demonstrating the adage ...   
63          64           2  This quiet , introspective and entertaining in...   
81          82           3  Even fans of Ismail Merchant 's work , I suspe...   
116        117           4  A positively thrilling combination of ethnogra...   
156        157           5  Aggressive self-glorification and a manipulati...   
...        ...         ...                                                ...   
1937      1938          72  -LRB- Scherfig -RRB- has made a movie that wil...   
1965      1966          73             -LRB- An -RRB- absorbing documentary .   
1972      1973          74  Reeks of rot and hack work from start to finish .   
1983      1984          75  Plays like a series of vignettes -- clips of a...   
2005      2006          76                                                      

      Sentiment  word_tokens  phrase_length  POS_tags  
0             1          NaN            NaN       NaN  
63            4          NaN            NaN       NaN  
81            1          NaN            NaN       NaN  
116           3          NaN            NaN       NaN  
156           1          NaN            NaN       NaN  
...         ...          ...            ...       ...  
1937          3          NaN            NaN       NaN  
1965          3          NaN            NaN       NaN  
1972          2          NaN            NaN       NaN  
1983          1          NaN            NaN       NaN  
2005          1          NaN            NaN       NaN  

[76 rows x 7 columns]

In [94]:
for i, phrase in enumerate(train_additional_cols['Phrase']):
    # just a single letter or space
    if len(phrase)==1:
        train_additional_cols.drop(train_additional_cols.index[i], inplace=True)

In [95]:
train_additional_cols.reset_index(drop=True, inplace=True)

In [96]:
# stop words from NLTK
nltk_stop_words = corpus.stopwords.words('english')

In [97]:
# function that takes a word and returns true if it consists only of non-alphabetic characters 
def alpha_filter(w):
  # pattern to match word of non-alphabetical characters
  pattern = re.compile('^[^a-z]+$')
  if pattern.match(w):
    return True
  else:
    return False

In [98]:
# removes stopwords and puctuation from text provided
def remove_stopwords_and_punct(word_token_list):
    clean_word_token_list = []
    for word_token in word_token_list:
        print('word_token', word_token)
        if (word_token in nltk_stop_words) or (alpha_filter(word_token)):
            continue
        else:
            clean_word_token_list.append(word_token)
    return clean_word_token_list

This will loop will:
- 1. tokenize 
- 2. set to lowercase
- 3. removes puctuation and stop words

In [99]:
 train_additional_cols_num_rows = len(train_additional_cols.index)

In [100]:
for index in range(train_additional_cols_num_rows):
    phrase = train_additional_cols['Phrase'][index]
    sent_token = sent_tokenize(phrase.lower())
#     sent_token comes as a list, we need a string
    word_token = word_tokenize(sent_token[0])
    word_token_clean = remove_stopwords_and_punct(word_token)
    train_additional_cols["word_tokens"][index] = word_token_clean
    train_additional_cols["phrase_length"][index] = len(phrase)
    

word_token a
word_token series
word_token of
word_token escapades
word_token demonstrating
word_token the
word_token adage
word_token that
word_token what
word_token is
word_token good
word_token for
word_token the
word_token goose
word_token is
word_token also
word_token good
word_token for
word_token the
word_token gander
word_token ,
word_token some
word_token of
word_token which
word_token occasionally
word_token amuses
word_token but
word_token none
word_token of
word_token which
word_token amounts
word_token to
word_token much
word_token of
word_token a
word_token story
word_token .
word_token this
word_token quiet
word_token ,
word_token introspective
word_token and
word_token entertaining
word_token independent
word_token is
word_token worth
word_token seeking
word_token .
word_token even
word_token fans
word_token of
word_token ismail
word_token merchant
word_token 's
word_token work
word_token ,
word_token i
word_token suspect
word_token ,
word_token would
word_token have
wor

word_token a
word_token vile
word_token ,
word_token incoherent
word_token mess
word_token ...
word_token a
word_token scummy
word_token ripoff
word_token of
word_token david
word_token cronenberg
word_token 's
word_token brilliant
word_token `
word_token videodrome
word_token .
word_token '
word_token first
word_token ,
word_token for
word_token a
word_token movie
word_token that
word_token tries
word_token to
word_token be
word_token smart
word_token ,
word_token it
word_token 's
word_token kinda
word_token dumb
word_token .
word_token i
word_token was
word_token sent
word_token a
word_token copyof
word_token this
word_token film
word_token to
word_token review
word_token on
word_token dvd
word_token .
word_token ...
word_token silly
word_token humbuggery
word_token ...
word_token is
word_token n't
word_token as
word_token sharp
word_token as
word_token the
word_token original
word_token ...
word_token despite
word_token some
word_token visual
word_token virtues
word_token ,
word_tok

word_token what
word_token sets
word_token this
word_token romantic
word_token comedy
word_token apart
word_token from
word_token most
word_token hollywood
word_token romantic
word_token comedies
word_token is
word_token its
word_token low-key
word_token way
word_token of
word_token tackling
word_token what
word_token seems
word_token like
word_token done-to-death
word_token material
word_token .
word_token the
word_token film
word_token 's
word_token constant
word_token mood
word_token of
word_token melancholy
word_token and
word_token its
word_token unhurried
word_token narrative
word_token are
word_token masterfully
word_token controlled
word_token .
word_token barry
word_token sonnenfeld
word_token owes
word_token frank
word_token the
word_token pug
word_token big
word_token time
word_token one
word_token gets
word_token the
word_token impression
word_token the
word_token creators
word_token of
word_token do
word_token n't
word_token ask
word_token do
word_token n't
word_token tell

word_token a
word_token film
word_token without
word_token surprise
word_token geared
word_token toward
word_token maximum
word_token comfort
word_token and
word_token familiarity
word_token .
word_token definitely
word_token a
word_token crowd-pleaser
word_token ,
word_token but
word_token then
word_token ,
word_token so
word_token was
word_token the
word_token roman
word_token colosseum
word_token .
word_token here
word_token is
word_token a
word_token vh1
word_token behind
word_token the
word_token music
word_token special
word_token that
word_token has
word_token something
word_token a
word_token little
word_token more
word_token special
word_token behind
word_token it
word_token :
word_token music
word_token that
word_token did
word_token n't
word_token sell
word_token many
word_token records
word_token but
word_token helped
word_token change
word_token a
word_token nation
word_token .
word_token kids
word_token will
word_token love
word_token its
word_token fantasy
word_token and

word_token a
word_token buoyant
word_token romantic
word_token comedy
word_token about
word_token friendship
word_token ,
word_token love
word_token ,
word_token and
word_token the
word_token truth
word_token that
word_token we
word_token 're
word_token all
word_token in
word_token this
word_token together
word_token .
word_token davis
word_token ...
word_token gets
word_token vivid
word_token performances
word_token from
word_token her
word_token cast
word_token and
word_token pulls
word_token off
word_token some
word_token deft
word_token ally
word_token mcbeal-style
word_token fantasy
word_token sequences
word_token .
word_token the
word_token sundance
word_token film
word_token festival
word_token has
word_token become
word_token so
word_token buzz-obsessed
word_token that
word_token fans
word_token and
word_token producers
word_token descend
word_token upon
word_token utah
word_token each
word_token january
word_token to
word_token ferret
word_token out
word_token the
word_token n

...

word_token an
word_token indispensable
word_token peek
word_token at
word_token the
word_token art
word_token and
word_token the
word_token agony
word_token of
word_token making
word_token people
word_token laugh
word_token .
word_token judging
word_token by
word_token those
word_token standards
word_token ,
word_token `
word_token scratch
word_token '
word_token is
word_token a
word_token pretty
word_token decent
word_token little
word_token documentary
word_token .
word_token does
word_token point
word_token the
word_token way
word_token for
word_token adventurous
word_token indian
word_token filmmakers
word_token toward
word_token a
word_token crossover
word_token into
word_token nonethnic
word_token markets
word_token .
word_token a
word_token direct-to-void
word_token release
word_token ,
word_token heading
word_token nowhere
word_token .
word_token whether
word_token jason
word_token x
word_token is
word_token this
word_token bad
word_token on
word_token purpose
word_token is
wor

word_token it
word_token turns
word_token out
word_token to
word_token be
word_token smarter
word_token and
word_token more
word_token diabolical
word_token than
word_token you
word_token could
word_token have
word_token guessed
word_token at
word_token the
word_token beginning
word_token .
word_token in
word_token terms
word_token of
word_token execution
word_token this
word_token movie
word_token is
word_token careless
word_token and
word_token unfocused
word_token .
word_token your
word_token nightmares
word_token ,
word_token on
word_token the
word_token other
word_token hand
word_token ,
word_token will
word_token be
word_token anything
word_token but
word_token .
word_token a
word_token slick
word_token ,
word_token engrossing
word_token melodrama
word_token .
word_token this
word_token picture
word_token is
word_token murder
word_token by
word_token numbers
word_token ,
word_token and
word_token as
word_token easy
word_token to
word_token be
word_token bored
word_token by
word_t

word_token the
word_token movie
word_token ends
word_token with
word_token outtakes
word_token in
word_token which
word_token most
word_token of
word_token the
word_token characters
word_token forget
word_token their
word_token lines
word_token and
word_token just
word_token utter
word_token `
word_token uhhh
word_token ,
word_token '
word_token which
word_token is
word_token better
word_token than
word_token most
word_token of
word_token the
word_token writing
word_token in
word_token the
word_token movie
word_token .
word_token frei
word_token assembles
word_token a
word_token fascinating
word_token profile
word_token of
word_token a
word_token deeply
word_token humanistic
word_token artist
word_token who
word_token ,
word_token in
word_token spite
word_token of
word_token all
word_token that
word_token he
word_token 's
word_token witnessed
word_token ,
word_token remains
word_token surprisingly
word_token idealistic
word_token ,
word_token and
word_token retains
word_token an
word_t

word_token ...
word_token the
word_token maudlin
word_token way
word_token its
word_token story
word_token unfolds
word_token suggests
word_token a
word_token director
word_token fighting
word_token against
word_token the
word_token urge
word_token to
word_token sensationalize
word_token his
word_token material
word_token .
word_token too
word_token many
word_token scenarios
word_token in
word_token which
word_token the
word_token hero
word_token might
word_token have
word_token an
word_token opportunity
word_token to
word_token triumphantly
word_token sermonize
word_token ,
word_token and
word_token too
word_token few
word_token that
word_token allow
word_token us
word_token to
word_token wonder
word_token for
word_token ourselves
word_token if
word_token things
word_token will
word_token turn
word_token out
word_token okay
word_token .
word_token a
word_token flawed
word_token film
word_token but
word_token an
word_token admirable
word_token one
word_token that
word_token tries
word_

word_token it
word_token gets
word_token bogged
word_token down
word_token by
word_token hit-and-miss
word_token topical
word_token humour
word_token before
word_token getting
word_token to
word_token the
word_token truly
word_token good
word_token stuff
word_token .
word_token between
word_token bursts
word_token of
word_token automatic
word_token gunfire
word_token ,
word_token the
word_token story
word_token offers
word_token a
word_token trenchant
word_token critique
word_token of
word_token capitalism
word_token .
word_token in
word_token addition
word_token to
word_token gluing
word_token you
word_token to
word_token the
word_token edge
word_token of
word_token your
word_token seat
word_token ,
word_token changing
word_token lanes
word_token is
word_token also
word_token a
word_token film
word_token of
word_token freshness
word_token ,
word_token imagination
word_token and
word_token insight
word_token .
word_token lasker
word_token 's
word_token canny
word_token ,
word_token med

In [101]:
# check data to make sure tokens match sentences at the beginning and end
train_additional_cols.head()
train_additional_cols.tail()

PhraseId  SentenceId                                             Phrase  \
0         1           1  A series of escapades demonstrating the adage ...   
1        64           2  This quiet , introspective and entertaining in...   
2        82           3  Even fans of Ismail Merchant 's work , I suspe...   
3       117           4  A positively thrilling combination of ethnogra...   
4       157           5  Aggressive self-glorification and a manipulati...   

   Sentiment                                        word_tokens  \
0          1  [series, escapades, demonstrating, adage, good...   
1          4  [quiet, introspective, entertaining, independe...   
2          1  [even, fans, ismail, merchant, 's, work, suspe...   
3          3  [positively, thrilling, combination, ethnograp...   
4          1  [aggressive, self-glorification, manipulative,...   

   phrase_length  POS_tags  
0          188.0       NaN  
1           74.0       NaN  
2          100.0       NaN  
3          152.0       NaN  
4           60.0       NaN

PhraseId  SentenceId                                             Phrase  \
8522    155985        8540  ... either you 're willing to go with this cla...   
8523    155998        8541  Despite these annoyances , the capable Claybur...   
8524    156022        8542  -LRB- Tries -RRB- to parody a genre that 's al...   
8525    156032        8543  The movie 's downfall is to substitute plot fo...   
8526    156040        8544  The film is darkly atmospheric , with Herrmann...   

      Sentiment                                        word_tokens  \
8522          2  [either, 're, willing, go, claustrophobic, con...   
8523          2  [despite, annoyances, capable, clayburgh, tamb...   
8524          1  [-lrb-, tries, -rrb-, parody, genre, 's, alrea...   
8525          1  [movie, 's, downfall, substitute, plot, person...   
8526          2  [film, darkly, atmospheric, herrmann, quietly,...   

      phrase_length  POS_tags  
8522           82.0       NaN  
8523          152.0       NaN  
8524           81.0       NaN  
8525           61.0       NaN  
8526          137.0       NaN

#### POS tagging, grammar rules phrase extraction

This loop will tag each list of tokens

In [102]:
for index, token_list in enumerate(train_additional_cols['word_tokens']):
    pos_tokens = pos_tag(token_list)
    train_additional_cols["POS_tags"][index] = pos_tokens

In [103]:
# check tags at the beginning and end
train_additional_cols.head()
train_additional_cols.tail()

PhraseId  SentenceId                                             Phrase  \
0         1           1  A series of escapades demonstrating the adage ...   
1        64           2  This quiet , introspective and entertaining in...   
2        82           3  Even fans of Ismail Merchant 's work , I suspe...   
3       117           4  A positively thrilling combination of ethnogra...   
4       157           5  Aggressive self-glorification and a manipulati...   

   Sentiment                                        word_tokens  \
0          1  [series, escapades, demonstrating, adage, good...   
1          4  [quiet, introspective, entertaining, independe...   
2          1  [even, fans, ismail, merchant, 's, work, suspe...   
3          3  [positively, thrilling, combination, ethnograp...   
4          1  [aggressive, self-glorification, manipulative,...   

   phrase_length                                           POS_tags  
0          188.0  [(series, NN), (escapades, VBZ), (demonstratin...  
1           74.0  [(quiet, JJ), (introspective, JJ), (entertaini...  
2          100.0  [(even, RB), (fans, NNS), (ismail, VBP), (merc...  
3          152.0  [(positively, RB), (thrilling, VBG), (combinat...  
4           60.0  [(aggressive, JJ), (self-glorification, NN), (...

PhraseId  SentenceId                                             Phrase  \
8522    155985        8540  ... either you 're willing to go with this cla...   
8523    155998        8541  Despite these annoyances , the capable Claybur...   
8524    156022        8542  -LRB- Tries -RRB- to parody a genre that 's al...   
8525    156032        8543  The movie 's downfall is to substitute plot fo...   
8526    156040        8544  The film is darkly atmospheric , with Herrmann...   

      Sentiment                                        word_tokens  \
8522          2  [either, 're, willing, go, claustrophobic, con...   
8523          2  [despite, annoyances, capable, clayburgh, tamb...   
8524          1  [-lrb-, tries, -rrb-, parody, genre, 's, alrea...   
8525          1  [movie, 's, downfall, substitute, plot, person...   
8526          2  [film, darkly, atmospheric, herrmann, quietly,...   

      phrase_length                                           POS_tags  
8522           82.0  [(either, DT), ('re, VBP), (willing, JJ), (go,...  
8523          152.0  [(despite, IN), (annoyances, NNS), (capable, J...  
8524           81.0  [(-lrb-, JJ), (tries, NNS), (-rrb-, VBP), (par...  
8525           61.0  [(movie, NN), ('s, POS), (downfall, NN), (subs...  
8526          137.0  [(film, NN), (darkly, RB), (atmospheric, JJ), ...

In [104]:
# an ADJPH chunk should be formed whenever the chunker finds adverb (RB) followed by an adjective (JJ).
grammar_adjph = "ADJPH: {<RB.?>+<JJ.?>}"
# an ADVPH chunk should be formed whenever the chunker finds 2 consecutive adverbs ('RB')
grammar_advph = "ADVPH: {<RB>+<RB>}"
# an VBPH chunk should be formed whenever the chunker finds verb (VB) followed by a noun (NN).
grammar_vbph = "VBPH: {<VB.?>+<NN.?>}"
# an NPH chunk should be formed whenever the chunker finds a determiner (DT) followed by a noun (NN). We simply choose to define noun phrase as determiner followed by a noun of any kind.
grammar_nph = "NPH: {<DT>+<NN.?>}"

In [105]:
# function toimport the nltk parser to process each sentence
def create_chunk_parser(grammar_rules):
    return RegexpParser(grammar_rules)

This function will do the following:
- parse text based on parser provided
- get the actual phrase
- calculate frequency for most_common phrases (log only, we can add a return value)
- show the length of phrases sentences (log only)

In [106]:
def parse_phrases(sent, chunk_parser, label):
    tags = []
    phrases = []

    if len(sent) > 0:
#         print('sent', sent)
        tree = chunk_parser.parse(sent)
        for subtree in tree.subtrees():
            if subtree.label() == label:
                tags.append(subtree)
    # Visualizing the actual phrase
    for sent in tags:
        temp = ''
        for w, t in sent:
            temp += w+ ' '    
        phrases.append(temp)
    print('phrases: ', phrases)
    # top 10 phrases
    freq = FreqDist(phrases)
    print('Top phrases by frequency: ')
    for word, freq in freq.most_common(10):
        print(word, freq)
    print("Length of {label} phrase sentences: ".format(label=label), len(tags))
    return phrases

##### Create parsers and parse the texts using the rules/parsers defined

In [107]:
adjph_parser = create_chunk_parser(grammar_adjph)
advph_parser = create_chunk_parser(grammar_advph)
vbph_parser = create_chunk_parser(grammar_vbph)
nph_parser = create_chunk_parser(grammar_nph)

Add more cols for grammar parser results

In [108]:
train_additional_cols["adjph"] = np.nan
train_additional_cols["advph"] = np.nan
train_additional_cols["vbph"] = np.nan
train_additional_cols["nph"] = np.nan

In [109]:
for index in range(train_additional_cols_num_rows):
    pos_tree = train_additional_cols['POS_tags'][index]
    if parse_phrases(pos_tree, adjph_parser, "ADJPH"):
        train_additional_cols["adjph"][index] = parse_phrases(pos_tree, adjph_parser, "ADJPH")
    else:
        train_additional_cols["adjph"][index] = 'no ADJPH phrases detected'

phrases:  ['also good ']
Top phrases by frequency: 
also good  1
Length of ADJPH phrase sentences:  1
phrases:  ['also good ']
Top phrases by frequency: 
also good  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['nearly epic ']
Top phrases by frequency: 
nearly epic  1
Length of ADJPH phrase sentences:  1
phrases:  ['nearly epic ']
Top phrases by frequency: 
nearly epic  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Lengt

phrases:  ['perhaps snuck ']
Top phrases by frequency: 
perhaps snuck  1
Length of ADJPH phrase sentences:  1
phrases:  ['perhaps snuck ']
Top phrases by frequency: 
perhaps snuck  1
Length of ADJPH phrase sentences:  1
phrases:  ['far disappointing ']
Top phrases by frequency: 
far disappointing  1
Length of ADJPH phrase sentences:  1
phrases:  ['far disappointing ']
Top phrases by frequency: 
far disappointing  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['decidedly unoriginal ']
Top phrases by frequency: 
decidedly unoriginal  1
Length of ADJPH phrase sentences:  1
phrases:  ['decidedly unoriginal ']
Top phrases by frequency: 
decidedly unoriginal  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase se

phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ["n't much "]
Top phrases by frequency: 
n't much  1
Length of ADJPH phrase sentences:  1
phrases:  ["n't much "]
Top phrases by frequency: 
n't much  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['silly stupid ']
Top phrases by frequency: 
silly stupid  1
Length of ADJPH phrase sentences:  1
phrases:  ['silly stupid ']
Top phrases by frequency: 
silly stupid  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['merely -lrb- ', 'repeatedly undercut ']
Top phrases by frequency: 
merely -lrb-  1
repeatedly undercut  1
Length of ADJPH phrase sentences:  2
phrases:  ['merely -lrb- ', 'repeatedly unde

Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['nearly impossible ']
Top phrases by frequency: 
nearly impossible  1
Length of ADJPH phrase sentences:  1
phrases:  ['nearly impossible ']
Top phrases by frequency: 
nearly impossible  1
Length of ADJPH phrase sentences:  1
phrases:  ['amy matthew ']
Top phrases by frequency: 
amy matthew  1
Length of ADJPH phrase sentences:  1
phrases:  ['amy matthew ']
Top phrases by frequency: 
amy matthew  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['thoroughly entertaining ']
Top phrases by frequency: 
thoroughly entertaining  1
Length of ADJPH phrase sentences:  1
phrases:  ['thoroughly entertaining ']
Top phrases by frequency: 
thoroughly entertaining  1
Length of ADJPH phrase sentences: 

phrases:  ['tart little ']
Top phrases by frequency: 
tart little  1
Length of ADJPH phrase sentences:  1
phrases:  ['tart little ']
Top phrases by frequency: 
tart little  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  ['ultimately worthwhile ']
Top phrases by frequency: 
ultimately worthwhile  1
Length of ADJPH phrase sentences:  1
phrases:  ['ultimately worthwhile ']
Top phrases by frequency: 
ultimately worthwhile  1
Length of ADJPH phrase sentences: 

phrases:  ['absolutely amazing ']
Top phrases by frequency: 
absolutely amazing  1
Length of ADJPH phrase sentences:  1
phrases:  ['absolutely amazing ']
Top phrases by frequency: 
absolutely amazing  1
Length of ADJPH phrase sentences:  1
phrases:  ['really quite funny ']
Top phrases by frequency: 
really quite funny  1
Length of ADJPH phrase sentences:  1
phrases:  ['really quite funny ']
Top phrases by frequency: 
really quite funny  1
Length of ADJPH phrase sentences:  1
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH phrase sentences:  0
phrases:  []
Top phrases by frequency: 
Length of ADJPH ph

In [110]:
train_additional_cols.head()

PhraseId  SentenceId                                             Phrase  \
0         1           1  A series of escapades demonstrating the adage ...   
1        64           2  This quiet , introspective and entertaining in...   
2        82           3  Even fans of Ismail Merchant 's work , I suspe...   
3       117           4  A positively thrilling combination of ethnogra...   
4       157           5  Aggressive self-glorification and a manipulati...   

   Sentiment                                        word_tokens  \
0          1  [series, escapades, demonstrating, adage, good...   
1          4  [quiet, introspective, entertaining, independe...   
2          1  [even, fans, ismail, merchant, 's, work, suspe...   
3          3  [positively, thrilling, combination, ethnograp...   
4          1  [aggressive, self-glorification, manipulative,...   

   phrase_length                                           POS_tags  \
0          188.0  [(series, NN), (escapades, VBZ), (demonstratin...   
1           74.0  [(quiet, JJ), (introspective, JJ), (entertaini...   
2          100.0  [(even, RB), (fans, NNS), (ismail, VBP), (merc...   
3          152.0  [(positively, RB), (thrilling, VBG), (combinat...   
4           60.0  [(aggressive, JJ), (self-glorification, NN), (...   

                       adjph  advph  vbph  nph  
0               [also good ]    NaN   NaN  NaN  
1  no ADJPH phrases detected    NaN   NaN  NaN  
2  no ADJPH phrases detected    NaN   NaN  NaN  
3  no ADJPH phrases detected    NaN   NaN  NaN  
4  no ADJPH phrases detected    NaN   NaN  NaN

In [111]:
# see how adjective phrase compares to the whole review
for index in range(train_additional_cols_num_rows):
    if train_additional_cols['adjph'][index]!="no ADJPH phrases detected":
        print(index)
        print(train_additional_cols['Phrase'][index], train_additional_cols['Sentiment'][index], train_additional_cols['adjph'][index])
        print('------next item-----------')

0
A series of escapades demonstrating the adage that what is good for the goose is also good for the gander , some of which occasionally amuses but none of which amounts to much of a story . 1 ['also good ']
------next item-----------
5
A comedy-drama of nearly epic proportions rooted in a sincere performance by the title character undergoing midlife crisis . 4 ['nearly epic ']
------next item-----------
13
Fresnadillo has something serious to say about the ways in which extravagant chance can distort our perspective and throw us off the path of good sense . 3 ['path good ']
------next item-----------
17
Like a less dizzily gorgeous companion to Mr. Wong 's In the Mood for Love -- very much a Hong Kong movie despite its mainland setting . 2 ['dizzily gorgeous ', 'love much hong ']
------next item-----------
25
It arrives with an impeccable pedigree , mongrel pep , and almost indecipherable plot complications . 2 ['almost indecipherable ']
------next item-----------
29
More vaudeville s

Among the many pleasures are the lively intelligence of the artists and their perceptiveness about their own situations . 3 ['lively intelligence ']
------next item-----------
4874
Diaz , Applegate , Blair and Posey are suitably kooky which should appeal to women and they strip down often enough to keep men alert , if not amused . 3 ['often enough ']
------next item-----------
4875
Plotless collection of moronic stunts is by far the worst movie of the year . 0 ['far worst ']
------next item-----------
4883
Noyce creates a film of near-hypnotic physical beauty even as he tells a story as horrifying as any in the heart-breakingly extensive annals of white-on-black racism . 2 ['heart-breakingly extensive ']
------next item-----------
4885
Melds derivative elements into something that is often quite rich and exciting , and always a beauty to behold . 4 ['often quite rich ']
------next item-----------
4888
It is n't that Stealing Harvard is a horrible movie -- if only it were that grand a f

This function will print top 50 tags and their frequency based on POS tag list provided provided ie we can supply adjective POS token tree and tagged text.

In [112]:
def get_top50_pos_tokens(pos_list, taggedtext):
    pos_tokens = []
    freq_table = PrettyTable(['word', 'frequency'])
    for sentence in taggedtext:
        for word, pos in sentence:
            if pos in pos_list:
                if len(word)>1:
                    pos_tokens.append(word)
    freq_pos = FreqDist(pos_tokens)
    for word, freq in freq_pos.most_common(50):
        freq_table.add_row([word, freq])
    print(freq_table)

### Next steps

####  Frequency  work

In [113]:
#Create a function that pulls the most frequent word in each review
def mostFreq(corpus):
    freqDist = FreqDist(corpus)
    freqList = list(freqDist.keys())
    try: 
        first =  freqList[0]
    except IndexError: 
        first = "None"
    return first

#### Add adverb, verb, noun phrase analysis (rules already set up, I did adjective phrases as an example)

#### Run Naive Bayes to predict negative/positive review

- with stop words
- without stop words
- maybe one where we use only the POS extracted phrase associated with it? (could be optional)